<a href="https://colab.research.google.com/github/smcdonnell7/web.scraper.workers.dev/blob/master/Daily_Sales_with_Investment_Forecast_Steps.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [46]:
# @title Setup
from google.colab import auth
from google.cloud import bigquery
from google.colab import data_table

project = 'trupar' # Project ID inserted based on the query results selected to explore
location = 'US' # Location inserted based on the query results selected to explore
client = bigquery.Client(project=project, location=location)
data_table.enable_dataframe_formatter()
auth.authenticate_user()

# Result set loaded from BigQuery Query as a DataFrame

In [47]:
# Running this code will read results from your previous job

bigquery_query = """
WITH FirstAppearance AS (
    SELECT
        o_customer_id,
        MIN(created_at_utc) AS first_seen_customer_date
    FROM `trupar.exp_dailyimports.order_summary_ds`
    WHERE ordernumber IS NOT NULL AND internalstatus_id <> 'canceled'
    GROUP BY o_customer_id
),
FirstAppearanceUser AS (
    SELECT
        o_customer_user_id,
        MIN(created_at_utc) AS first_seen_user_date
    FROM `trupar.exp_dailyimports.order_summary_ds`
    WHERE ordernumber IS NOT NULL AND internalstatus_id <> 'canceled'
    GROUP BY o_customer_user_id
),
DataWithFirstAppearance AS (
    SELECT
        main.*,
        fa.first_seen_customer_date,
        fau.first_seen_user_date
    FROM `trupar.exp_dailyimports.order_summary_ds` main
    LEFT JOIN FirstAppearance fa ON main.o_customer_id = fa.o_customer_id
    LEFT JOIN FirstAppearanceUser fau ON main.o_customer_user_id = fau.o_customer_user_id
    WHERE ordernumber IS NOT NULL AND internalstatus_id <> 'canceled' AND price_subtotal > 0
)
SELECT
    DATE(created_at_utc) AS created_day,
    COUNT(DISTINCT order_id) AS distinct_order_count,
    COUNT(DISTINCT main.o_customer_id) AS distinct_customer_count,
    COUNT(DISTINCT IF(DATE(created_at_utc) = DATE(first_seen_customer_date), main.o_customer_id, NULL)) AS new_o_customer_count,
    COUNT(DISTINCT IF(DATE(created_at_utc) <> DATE(first_seen_customer_date), main.o_customer_id, NULL)) AS returning_o_customer_count,
    COUNT(DISTINCT main.o_customer_user_id) AS distinct_user_count,
    COUNT(DISTINCT IF(DATE(created_at_utc) = DATE(first_seen_user_date), main.o_customer_user_id, NULL)) AS new_o_customer_user_count,
    COUNT(DISTINCT IF(DATE(created_at_utc) <> DATE(first_seen_user_date), main.o_customer_user_id, NULL)) AS returning_o_customer_user_count,
    SUM(price_core) AS sum_price_core,
    SUM(CASE WHEN cost_core = 0 AND price_core > 0 THEN 0.9 * price_core ELSE cost_core END) AS sum_cost_core,
    SUM(price_ship) AS sum_price_ship,
    SUM(CASE WHEN cost_ship = 0 AND price_ship > 0 THEN 0.9 * price_ship ELSE cost_ship END) AS sum_cost_ship,
    SUM(CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) AS sum_price_subtotal,
    SUM(CASE WHEN cost_subtotal = 0 AND price_subtotal > 0 THEN 0.8 * price_subtotal ELSE cost_subtotal END) AS sum_cost_subtotal,
    SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) AS price_total,
    SUM(CASE WHEN cost_core = 0 AND price_core > 0 THEN 0.9 * price_core ELSE cost_core END +
        CASE WHEN cost_ship = 0 AND price_ship > 0 THEN 0.9 * price_ship ELSE cost_ship END +
        CASE WHEN cost_subtotal = 0 AND price_subtotal > 0 THEN 0.8 * price_subtotal ELSE cost_subtotal END) AS cost_total,
    (SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) -
    SUM(CASE WHEN cost_core = 0 AND price_core > 0 THEN 0.9 * price_core ELSE cost_core END +
        CASE WHEN cost_ship = 0 AND price_ship > 0 THEN 0.9 * price_ship ELSE cost_ship END +
        CASE WHEN cost_subtotal = 0 AND price_subtotal > 0 THEN 0.8 * price_subtotal ELSE cost_subtotal END)) AS profit_total,
    CASE WHEN SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) <> 0
         THEN (SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) -
              SUM(CASE WHEN cost_core = 0 AND price_core > 0 THEN 0.9 * price_core ELSE cost_core END +
                  CASE WHEN cost_ship = 0 AND price_ship > 0 THEN 0.9 * price_ship ELSE cost_ship END +
                  CASE WHEN cost_subtotal = 0 AND price_subtotal > 0 THEN 0.8 * price_subtotal ELSE cost_subtotal END)) /
              SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END)
         ELSE NULL END AS margin_total,
    CASE WHEN COUNT(DISTINCT order_id) <> 0
         THEN SUM(price_core + price_ship + CASE WHEN price_subtotal <> 0 THEN price_subtotal ELSE 0 END) /
              COUNT(DISTINCT order_id)
         ELSE NULL END AS average_order_value
FROM DataWithFirstAppearance main
GROUP BY DATE(created_at_utc)
"""

# Fetch the results into a DataFrame
results = client.query(bigquery_query).to_dataframe()
results

created_day  distinct_order_count  distinct_customer_count  \
0     2023-08-18                    48                       45   
1     2023-08-19                     2                        2   
2     2016-08-25                    35                       35   
3     2016-08-26                    29                       27   
4     2016-08-27                     7                        7   
...          ...                   ...                      ...   
3125  2017-12-10                     1                        1   
3126  2016-01-01                     1                        1   
3127  2015-12-27                     1                        1   
3128  2018-07-01                     1                        1   
3129  2015-02-15                     1                        1   

      new_o_customer_count  returning_o_customer_count  distinct_user_count  \
0                       14                          31                   45   
1                        0                           2                    2   
2                       21                          14                   35   
3                       11                          16                   27   
4                        7                           0                    7   
...                    ...                         ...                  ...   
3125                     1                           0                    1   
3126                     1                           0                    1   
3127                     1                           0                    1   
3128                     1                           0                    1   
3129                     1                           0                    1   

      new_o_customer_user_count  returning_o_customer_user_count  \
0                            14                               31   
1                             0                                2   
2                            21                               14   
3                            11                               16   
4                             7                                0   
...                         ...                              ...   
3125                          1                                0   
3126                          1                                0   
3127                          1                                0   
3128                          1                                0   
3129                          1                                0   

      sum_price_core  sum_cost_core  sum_price_ship  sum_cost_ship  \
0                0.0            0.0          713.73        876.457   
1                0.0            0.0            0.00          0.000   
2                0.0            0.0          557.27        553.270   
3                0.0            0.0          306.00        335.000   
4                0.0            0.0           79.00         77.100   
...              ...            ...             ...            ...   
3125             0.0            0.0           14.00         14.000   
3126             0.0            0.0           11.99         11.000   
3127             0.0            0.0            7.99         14.000   
3128             0.0            0.0           14.00          8.000   
3129             0.0            0.0            5.99          8.000   

      sum_price_subtotal  sum_cost_subtotal  price_total  cost_total  \
0               14943.66          11309.224     15657.39   12185.681   
1                1189.74            951.792      1189.74     951.792   
2                6478.56           4920.000      7035.83    5473.270   
3               10253.69           7451.600     10559.69    7786.600   
4                 674.52            516.230       753.52     593.330   
...                  ...                ...          ...         ...   
3125               58.20             29.680        72.20      43.680   
3126             

#Step 1: Data Preparation



In [48]:
from prophet import Prophet
import pandas as pd

# Columns to forecast
forecast_columns = ['distinct_order_count', 'distinct_customer_count', 'new_o_customer_count',
                    'returning_o_customer_count', 'distinct_user_count', 'new_o_customer_user_count',
                    'returning_o_customer_user_count', 'sum_price_core', 'sum_cost_core',
                    'sum_price_ship', 'sum_cost_ship', 'sum_price_subtotal', 'sum_cost_subtotal',
                    'price_total', 'cost_total', 'profit_total', 'margin_total', 'average_order_value']

# Determine the last date in the historical data
last_date = pd.to_datetime(results['created_day'].max())

# Step 2: Define Hiring Timeline and Impact

In [49]:
hiring_timeline = {
    1: {'Marketing Specialist': 1.2, 'Sales Representative': 1.2, 'Software Developer': 1.05},
    4: {'Operations Manager': 1.1, 'Sales Representative': 1.2},
    7: {'Customer Support Representative': 1.05, 'Data Analyst': 1.1},
    13: {'Sales Representative': 1.2, 'Software Developer': 1.05},
    19: {'Marketing Manager': 1.3, 'Product Manager': 1.2},
    25: {'UX/UI Designer': 1.1, 'Customer Support Representative': 1.05},
    31: {'Business Development Manager': 1.4, 'Data Analyst': 1.1}
}

# Step 3: Initialize Forecast Dictionary and Regressors

In [50]:
forecasts = {}
regressors = ['Marketing_Campaign_Effect', 'Sales_Outreach', 'Product_Launches',
              'Operational_Efficiency', 'Customer_Satisfaction', 'Data_Driven_Decisions',
              'UX_Improvements', 'New_Partnerships', 'Maturity_Phase_Effect']

# Step 4: Create Models and Generate Forecasts for Each Column

In [ ]:
for col in forecast_columns:
    temp_df = results[['created_day', col]].rename(columns={col: 'y', 'created_day': 'ds'})
    temp_df['ds'] = pd.to_datetime(temp_df['ds'])
    temp_df = temp_df.assign(**{reg: 0 for reg in regressors})
    model = Prophet(daily_seasonality=True)
    [model.add_regressor(reg) for reg in regressors]
    model.fit(temp_df)

# Step 4.5: Create Future Dates DataFrame and Initialize Regressors

In [52]:
future_dates = model.make_future_dataframe(periods=5*365)
future_dates = future_dates[future_dates['ds'] > last_date]
future_dates = future_dates.assign(**{reg: 0 for reg in regressors})

# Step 5: Adjust Regressors Based on Marketing Effects

In [53]:
    marketing_start_date = last_date + pd.DateOffset(months=3)
    for i in range(36):
        month_offset = i
        impact = 1 + (0.08 * (i+1))
        apply_date = marketing_start_date + pd.DateOffset(months=month_offset)
        future_dates.loc[future_dates['ds'] >= apply_date, 'Marketing_Campaign_Effect'] *= impact

# Step 6: Adjust Regressors Based on Hiring Timeline

In [54]:
    # Define the duration of the onboarding process
    onboarding_duration = 3

    # Iterate over the hiring timeline to adjust the Sales_Outreach effectiveness based on new hires
    for month_offset, roles in hiring_timeline.items():
        # Check if Sales Representatives are being hired in the current month
        if 'Sales Representative' in roles:
            # Get the multiplier for the Sales Representative role
            multiplier = roles['Sales Representative']

            # Apply the ramp-up effect for the onboarding duration
            for i in range(onboarding_duration):
                # Calculate the ramp-up effectiveness for the current month of onboarding
                ramp_up_effectiveness = (i + 1) / onboarding_duration * multiplier

                # Determine the date to apply the ramp-up effect
                apply_date = last_date + pd.DateOffset(months=month_offset + i)

                # Adjust the Sales_Outreach regressor based on the ramp-up effectiveness
                future_dates.loc[future_dates['ds'] == apply_date, 'Sales_Outreach'] *= ramp_up_effectiveness

# 6.5 Adjust Maturity Based on Sales

In [55]:
# Define the MoM multiplier for the Maturity Phase
maturity_multiplier = 1.10  # This represents a 10% growth

# Define the start date for this multiplier
start_date = pd.to_datetime("2024-07-01")

# Apply the multiplier to the future_dates DataFrame starting from the defined start_date
future_dates.loc[future_dates['ds'] >= start_date, 'Maturity_Phase_Effect'] = maturity_multiplier

# Step 7: Generate Forecast and Store in Dictionary

In [56]:
forecast = model.predict(future_dates)
forecasts[col] = forecast[['ds', 'yhat']]

# 7.5 Forecast Column Check

In [57]:
if col not in forecasts:
    print(f"Failed to generate forecast for {col}.")
else:
    print(f"Forecast generated for {col}.")

Forecast generated for average_order_value.


# Step 8: Combine Forecasts



In [58]:
for col in forecast_columns:
    if col not in forecasts:
        print(f"Missing forecast for column: {col}")
    else:
        try:
            forecast_df = pd.concat([forecasts[col].set_index('ds') for col in forecast_columns], axis=1)
            forecast_df = forecast_df.reset_index()
            forecast_df.columns = ['created_day'] + forecast_columns
        except KeyError as e:
            print(f"Error while processing forecast for {col}: {e}")

Missing forecast for column: distinct_order_count
Missing forecast for column: distinct_customer_count
Missing forecast for column: new_o_customer_count
Missing forecast for column: returning_o_customer_count
Missing forecast for column: distinct_user_count
Missing forecast for column: new_o_customer_user_count
Missing forecast for column: returning_o_customer_user_count
Missing forecast for column: sum_price_core
Missing forecast for column: sum_cost_core
Missing forecast for column: sum_price_ship
Missing forecast for column: sum_cost_ship
Missing forecast for column: sum_price_subtotal
Missing forecast for column: sum_cost_subtotal
Missing forecast for column: price_total
Missing forecast for column: cost_total
Missing forecast for column: profit_total
Missing forecast for column: margin_total
Error while processing forecast for average_order_value: 'distinct_order_count'


# Step 9: Combine Historical Data and Upload to BigQuery

In [59]:
historical_df = results[['created_day'] + forecast_columns]
combined_df = pd.concat([historical_df, forecast_df], axis=0).reset_index(drop=True)

# Function to upload DataFrame to BigQuery
def upload_to_bigquery(df, table_id):
    job_config = bigquery.LoadJobConfig(
        write_disposition = "WRITE_TRUNCATE",
    )
    job = client.load_table_from_dataframe(df, table_id, job_config=job_config)
    job.result()
    print(f"Uploaded {df.shape[0]} rows to {table_id}.")

table_id = "trupar.exp_dailyimports.o_daily_forecast"
upload_to_bigquery(combined_df, table_id)

Uploaded 4955 rows to trupar.exp_dailyimports.o_daily_forecast.


## Show descriptive statistics using describe()

In [60]:
forecast_df.describe()

distinct_order_count  distinct_customer_count  new_o_customer_count  \
count           1825.000000              1825.000000           1825.000000   
mean              28.541903                28.624892              7.798958   
std               13.614348                12.785346              6.088984   
min               -5.597219                -2.938772             -8.571557   
25%               16.207769                17.083409              2.758973   
50%               33.591461                33.378629              9.620310   
75%               40.157416                39.534557             12.476397   
max               46.866458                45.532498             17.916365   

       returning_o_customer_count  distinct_user_count  \
count                 1825.000000          1825.000000   
mean                    20.554348            28.472410   
std                      7.047640            12.794810   
min                      2.183347            -3.190065   
25%                     14.678783            16.928490   
50%                     23.098539            33.168904   
75%                     26.461933            39.415074   
max                     30.548563            45.487331   

       new_o_customer_user_count  returning_o_customer_user_count  \
count                1825.000000                      1825.000000   
mean                    7.759991                        20.655312   
std                     6.114600                         7.045120   
min                    -8.698928                         2.258066   
25%                     2.708966                        14.774055   
50%                     9.588145                        23.149869   
75%                    12.473223                        26.544217   
max                    17.914591                        30.705862   

       sum_price_core  sum_cost_core  sum_price_ship  sum_cost_ship  \
count     1825.000000    1825.000000     1825.000000    1825.000000   
mean       109.103333     200.432390      510.889050    1053.766260   
std         34.081534      57.936404      207.393945     275.539583   
min         27.764594      55.424838       14.311829     287.188034   
25%         82.541678     160.547860      326.502654     857.239083   
50%        111.450067     198.857812      591.079782    1092.610126   
75%        132.551268     240.503340      688.311652    1262.257221   
max        218.063705     384.825016      771.513398    1555.118335   

       sum_price_subtotal  sum_cost_subtotal   price_total    cost_total  \
count         1825.000000        1825.000000   1825.000000   1825.000000   
mean         13591.400121        9642.513736  14197.444912  10931.483246   
std           3963.678331        2866.568175   4183.299614   3188.691187   
min           2719.666857        1837.106653   2777.447537   2222.780945   
25%          10632.970053        7437.817829  11060.625166   8503.856907   
50%          14581.326560       10385.797016  15295.800060  11736.238312   
75%          16716.370230       11943.446347  17522.218267  13483.374975   
max          20306.157712       14325.349745  21195.631010  16271.006940   

       profit_total  margin_total  average_order_value  
count   1825.000000   1825.000000          1825.000000  
mean    3397.606300      0.222775           466.892448  
std     1019.291435      0.016237            70.248620  
min      605.189569      0.185043           271.484667  
25%     2649.774479      0.210843           413.412328  
50%     3649.692790      0.222845           466.252617  
75%     4195.568914      0.234409           525.857057  
max     5221.152043      0.268051           612.518072